## Препроцессинг данных

__Папка с данными на gdrive__

https://drive.google.com/drive/folders/1FeUwrVfxp09xAifiMngwtfrRZ8nhtj8T?usp=sharing



In [1]:
import pandas as pd
import numpy as np
import seaborn as sns
import folium
from matplotlib import pyplot as plt
from matplotlib import colors
from os import listdir
from tqdm import tqdm
from sklearn.decomposition import PCA
from sklearn.preprocessing import MinMaxScaler, StandardScaler
from snippets import *

%matplotlib inline

In [2]:
DATA_PATH = "../../data"

GPS_PATH = f"{DATA_PATH}/gps_data.csv"
ACCEL_PATH = f"{DATA_PATH}/accel_data.csv"

listdir(DATA_PATH)

['data_good_right_dates',
 'drivers_stats.csv',
 'gps_data.csv',
 'unlabeled',
 'gps_data_raw.csv',
 'good_data',
 'matched_data.csv',
 'points_stats.csv',
 'accel_data.csv',
 'accel_data_raw.csv',
 'drivers_with_gps_and_sl_problems',
 'gps_stats.csv',
 'rides_of_drivers.csv',
 'accel_stats.csv']

## Датасет GPS

In [3]:
df_gps = pd.read_csv(GPS_PATH, parse_dates=[0, 3])
describe(df_gps)

dtypes        count                           mean  \
time           datetime64[ns]      5050292  2020-07-31 17:37:31.378774272   
lat                   float64  5.05029e+06                         55.743   
lon                   float64  5.05029e+06                        37.6021   
gps_time       datetime64[ns]      5050292  2020-07-31 17:37:28.866647296   
driver_hash             int64  5.05029e+06                    3.03558e+17   
fraud                   int64  5.05029e+06                      -0.767609   
gps_delta             float64  5.05029e+06                        6.85008   
gps_distance          float64  5.05029e+06                         19.588   
gps_speed             float64  5.05029e+06                        5.64977   
gps_accel             float64  5.05029e+06                     -0.0740194   
tm_delta              float64  5.05029e+06                        6.87986   
tm_distance           float64  5.05029e+06                        20.2285   
tm_speed              float64  5.05029e+06                        6.30422   
tm_accel              float64  5.05029e+06                      0.0702472   
diff_time             float64  5.05029e+06                       0.686299   
diff_distance         float64  5.05029e+06                         0.8069   
diff_speed            float64  5.05029e+06                       0.697568   
diff_accel            float64  5.05029e+06                       0.594992   

                               min                            25%  \
time           2015-03-01 03:00:02  2020-11-20 07:07:20.750000128   
lat                          42.98                        55.6674   
lon                        26.1013                        37.5009   
gps_time       2015-03-01 03:00:02  2020-11-20 07:07:20.750000128   
driver_hash           -9.21858e+18                   -4.06958e+18   
fraud                           -1                             -1   
gps_delta                        0                              2   
gps_distance                     0                              0   
gps_speed                        0                              0   
gps_accel                     -100                      -0.111111   
tm_delta                         0                              2   
tm_distance                      0                              0   
tm_speed                         0                              0   
tm_accel                      -100                      -0.111111   
diff_time                        0                              0   
diff_distance                    0                              0   
diff_speed                       0                              0   
diff_accel                       0                              0   

                               50%                            75%  \
time           2021-03-05 11:16:20  2021-06-03 21:19:25.750000128   
lat                        55.7496                        55.8242   
lon                        37.5848                        37.7032   
gps_time       2021-03-05 11:16:20  2021-06-03 21:19:25.750000128   
driver_hash            1.02237e+17                    4.79299e+18   
fraud                           -1                             -1   
gps_delta                        3                              3   
gps_distance                     5                             25   
gps_speed                        2                        9.66667   
gps_accel                        0                       0.111111   
tm_delta                         3                              3   
tm_distance                      5                             25   
tm_speed                         2                             10   
tm_accel                         0                       0.111111   
diff_time                        0                              0   
diff_distance                    0                              0   
diff_speed                       0                              0   
diff_

(5050292, 18)

## Датасет акселерометра

In [4]:
df_accel = pd.read_csv(ACCEL_PATH, parse_dates=[0])
describe(df_accel)

dtypes        count                           mean  \
time         datetime64[ns]      2172989  2020-11-22 12:54:59.282576896   
x                   float64  2.17299e+06                       0.368934   
y                   float64  2.17299e+06                         7.6569   
z                   float64  2.17299e+06                        3.83295   
lat                 float64  2.17299e+06                        55.7482   
lon                 float64  2.17299e+06                         37.601   
driver_hash           int64  2.17299e+06                   -1.12657e+17   
fraud                 int64  2.17299e+06                      -0.796897   
ac_delta            float64  2.17299e+06                        11.2106   
ac_distance         float64  2.17299e+06                         185.61   
ac_speed            float64  2.17299e+06                        78.3813   
ac_accel            float64  2.17299e+06                        28.7075   

                             min                  25%                  50%  \
time         2015-02-28 05:46:43  2020-12-18 06:53:34  2021-03-18 16:54:01   
x                       -71.1054            -0.371101             0.184359   
y                       -74.7916              7.63271              8.85376   
z                       -65.5062              2.01402              3.69992   
lat                      55.3163              55.6768              55.7512   
lon                      36.3143              37.5016              37.5863   
driver_hash         -9.21858e+18         -4.47912e+18         -4.14168e+17   
fraud                         -1                   -1                   -1   
ac_delta                       0                    0                    0   
ac_distance                    0                   11                   77   
ac_speed                       0                  100                  100   
ac_accel                    -100              28.7075              28.7075   

                             75%                  max         std  
time         2021-06-12 11:02:19  2021-08-29 00:03:16         NaN  
x                       0.785298              65.1529     2.36914  
y                        9.50019              55.2294      3.4034  
z                        5.35365              76.4756     2.73072  
lat                      55.8214              82.4343     0.16893  
lon                       37.686              108.856    0.376061  
driver_hash          4.43147e+18          9.20647e+18  5.3536e+18  
fraud                         -1                    1    0.509161  
ac_delta                       0                 3600      118.59  
ac_distance                  230                10000     399.524  
ac_speed                     100                  100     40.4896  
ac_accel                 28.7075                  100     37.3881

(2172989, 12)

## Пример отрисовки маршрутов

In [5]:
# [None, -1, 0, 1]
FORCE_FRAUD = None

# Выбор случайного водителя
driver_gps, driver_hash, driver_fraud = sample_driver(df_gps, FORCE_FRAUD)
driver_accel = df_accel[df_accel["driver_hash"] == driver_hash]

center = (driver_gps["lat"].mean(), driver_gps["lon"].mean())
m = folium.Map(location=center, zoom_start=10, legend=True)

# Маршрут по данным акселерометра
driver_accel = driver_accel.sort_values(by="time").reset_index(drop=True)
map_driver_points(m, driver_accel, driver_hash, label="accel", color="blue")

# Маршрут по данным  GPS
driver_gps = driver_gps.sort_values(by="gps_time").reset_index(drop=True)
map_driver_points(m, driver_gps, driver_hash, label="gps")

folium.map.LayerControl('topleft', collapsed= False).add_to(m)
m

## Слияние датасетов GPS и акселерометра по "gps_time" и "time"

In [6]:
MERGE_TOLERANCE = "180s"

colmap = {c: f"ac_{c}" for c in df_accel.columns if not "ac" in c}
ac_columns = [colmap[c] if c in colmap else c for c in df_accel.columns]
newcolmap = dict(zip(df_accel.columns, ac_columns))
newcolmap.pop("driver_hash")

df_left = df_gps.sort_values(by=["gps_time"])
df_right = df_accel.sort_values(by=["time"]).rename(columns=newcolmap)
df_merged = pd.merge_asof(df_left, df_right,
                          left_on="gps_time",
                          right_on="ac_time",
                          direction="nearest",
                          by="driver_hash",
                          tolerance=pd.Timedelta("180s"),
                          allow_exact_matches=False
                         )

display(f"GPS size:      {df_gps.index.shape[0]}")
display(f"GPS matched:   {df_merged[df_merged['fraud'].notna()].shape[0]}")
display(f"Accel size:    {df_accel.index.shape[0]}")
display(f"Accel matched: {df_merged[df_merged['ac_fraud'].notna()].shape[0]}")

'GPS size:      5050292'

'GPS matched:   5050292'

'Accel size:    2172989'

'Accel matched: 3025840'

### Статистика слияния по водителям

In [7]:
results = df_merged.groupby(by="driver_hash") \
    .count() \
    .loc[:,["fraud", "ac_fraud"]] \
    .rename(columns={"fraud": "recs_total", "ac_fraud": "recs_matched"})
    
results["gps_total"] = df_gps.groupby("driver_hash").count()["fraud"].apply(float)
results["gps_matched"] = results["recs_matched"] / results["gps_total"]
results["accel_total"] = df_accel.groupby("driver_hash").count()["fraud"].fillna(0)
results["accel_matched"] = results["recs_matched"] / results["accel_total"]

results

recs_total  recs_matched  gps_total  gps_matched  \
driver_hash                                                              
-9218579406240981296       17592         14317    17592.0     0.813836   
-9148378939849570226        2430          1053     2430.0     0.433333   
-9090289600630456229        4458          1576     4458.0     0.353522   
-9073383204587901813       12885         11456    12885.0     0.889096   
-9067392653059450527       14939          3821    14939.0     0.255773   
...                          ...           ...        ...          ...   
 8979134000488028450       24378         18510    24378.0     0.759291   
 8979322487342770688        1060           767     1060.0     0.723585   
 9028001926696043346       17144          7459    17144.0     0.435079   
 9142516420276355425        7481          4640     7481.0     0.620238   
 9206466041403273735       19370         15096    19370.0     0.779350   

                      accel_total  accel_matched  
driver_hash                                       
-9218579406240981296       9992.0       1.432846  
-9148378939849570226        889.0       1.184477  
-9090289600630456229        912.0       1.728070  
-9073383204587901813       9982.0       1.147666  
-9067392653059450527       9998.0       0.382176  
...                           ...            ...  
 8979134000488028450       9998.0       1.851370  
 8979322487342770688       3404.0       0.225323  
 9028001926696043346       9998.0       0.746049  
 9142516420276355425       4656.0       0.996564  
 9206466041403273735       9989.0       1.511262  

[317 rows x 6 columns]

In [8]:
df_matched = df_merged.dropna().drop(columns=["ac_fraud"])
df_matched

time        lat        lon            gps_time  \
966     2015-03-01 05:39:22  55.824982  37.834086 2015-03-01 05:39:22   
967     2015-03-01 05:39:25  55.825013  37.834061 2015-03-01 05:39:25   
968     2015-03-01 05:39:28  55.825042  37.834034 2015-03-01 05:39:28   
969     2015-03-01 05:39:31  55.825057  37.834022 2015-03-01 05:39:31   
970     2015-03-01 05:39:34  55.825046  37.834022 2015-03-01 05:39:34   
...                     ...        ...        ...                 ...   
5048614 2021-08-27 17:12:18  55.604352  37.497382 2021-08-27 17:12:18   
5048615 2021-08-27 17:12:21  55.604120  37.497680 2021-08-27 17:12:21   
5048616 2021-08-27 17:12:23  55.603934  37.497906 2021-08-27 17:12:23   
5048617 2021-08-27 17:12:26  55.603682  37.498205 2021-08-27 17:12:26   
5048618 2021-08-27 17:12:29  55.603522  37.498388 2021-08-27 17:12:29   

                 driver_hash  fraud  gps_delta  gps_distance  gps_speed  \
966      4633179079544742811      0        3.0           4.0   1.333333   
967      4633179079544742811      0        3.0           4.0   1.333333   
968      4633179079544742811      0        3.0           4.0   1.333333   
969      4633179079544742811      0        3.0           2.0   0.666667   
970      4633179079544742811      0        3.0           1.0   0.333333   
...                      ...    ...        ...           ...        ...   
5048614  2423204062901461132     -1        3.0          30.0  10.000000   
5048615  2423204062901461132     -1        3.0          32.0  10.666667   
5048616  2423204062901461132     -1        2.0          25.0  12.500000   
5048617  2423204062901461132     -1        3.0          34.0  11.333333   
5048618  2423204062901461132     -1        3.0          21.0   7.000000   

         gps_accel  ...             ac_time      ac_x      ac_y      ac_z  \
966       0.000000  ... 2015-03-01 05:42:20  0.133682  8.409241  4.568481   
967       0.000000  ... 2015-03-01 05:42:20  0.133682  8.409241  4.568481   
968       0.000000  ... 2015-03-01 05:42:20  0.133682  8.409241  4.568481   
969      -0.222222  ... 2015-03-01 05:42:20  0.133682  8.409241  4.568481   
970      -0.111111  ... 2015-03-01 05:42:20  0.133682  8.409241  4.568481   
...            ...  ...                 ...       ...       ...       ...   
5048614  -1.000000  ... 2021-08-27 17:09:29  0.294487  9.339781  3.356671   
5048615   0.222222  ... 2021-08-27 17:09:29  0.294487  9.339781  3.356671   
5048616   0.916666  ... 2021-08-27 17:09:29  0.294487  9.339781  3.356671   
5048617  -0.388889  ... 2021-08-27 17:09:29  0.294487  9.339781  3.356671   
5048618  -1.444444  ... 2021-08-27 17:09:29  0.294487  9.339781  3.356671   

            ac_lat     ac_lon  ac_delta  ac_distance  ac_speed  ac_accel  
966      55.825185  37.833479    3600.0      10000.0  2.777778 -0.027006  
967      55.825185  37.833479    3600.0      10000.0  2.777778 -0.027006  
968      55.825185  37.833479    3600.0      10000.0  2.777778 -0.027006  
969      55.825185  37.833479    3600.0      10000.0  2.777778 -0.027006  
970      55.825185  37.833479    3600.0      10000.0  2.777778 -0.027006  
...            ...        ...       ...          ...       ...       ...  
5048614  55.604776  37.492613      60.0        246.0  4.100000 -1.598333  
5048615  55.604776  37.492613      60.0        246.0  4.100000 -1.598333  
5048616  55.604776  37.492613      60.0        246.0  4.100000 -1.598333  
5048617  55.604776  37.492613      60.0        246.0  4.100000 -1.598333  
5048618  55.604776  37.492613      60.0        246.0  4.100000 -1.598333  

[3025840 rows x 28 columns]

In [9]:
df_matched.to_csv(f"{DATA_PATH}/matched_data.csv", index=False)
'Done'

'Done'

## Пример разбивки на поездки объединенного датасета

In [10]:
ROUTE_SPLIT_COLUMN = "gps_delta"
ROUTE_SPLIT_INTERVAL = "60s"

routs_idx = pd.to_timedelta(df_matched[ROUTE_SPLIT_COLUMN], unit="seconds") \
    .dt.round(ROUTE_SPLIT_INTERVAL) \
    .dt.total_seconds() \
    .cumsum().apply(int)

number_of_routs = len(routs_idx.unique())
display(f"Number of routs: {number_of_routs}")

'Number of routs: 1068'

In [17]:
# [None, -1, 0, 1]
FORCE_FRAUD = None

# Выбор случайного водителя
df_driver, driver_hash, driver_fraud = sample_driver(df_matched, FORCE_FRAUD)
driver_routs = routs_idx[df_driver.index]

center = (df_driver["lat"].mean(), df_driver["lon"].mean())
m = folium.Map(location=center, zoom_start=10, legend=True)
map_driver_points(m, df_driver, driver_hash, label="points", color="black", weight=12)

color = df_driver.head(1)["fraud"].replace({1:"red", 0:"green", -1:"yellow"}).values[0]

for rx in driver_routs.unique():
    fg = folium.FeatureGroup(name=f"route{rx}")
    gps_route = df_driver.loc[driver_routs == rx, ["lat", "lon"]]
    folium.PolyLine(gps_route, color="blue", weight=8, opacity=0.8).add_to(fg)
    accel_route = df_driver.loc[driver_routs == rx, ["ac_lat", "ac_lon"]]
    folium.PolyLine(accel_route, color=color, weight=6, opacity=0.8).add_to(fg)
    fg.add_to(m)

folium.map.LayerControl('topleft', collapsed=False).add_to(m)
m

## Разбивка на поездки

In [12]:
df_routs = df_matched.copy()
df_routs

time        lat        lon            gps_time  \
966     2015-03-01 05:39:22  55.824982  37.834086 2015-03-01 05:39:22   
967     2015-03-01 05:39:25  55.825013  37.834061 2015-03-01 05:39:25   
968     2015-03-01 05:39:28  55.825042  37.834034 2015-03-01 05:39:28   
969     2015-03-01 05:39:31  55.825057  37.834022 2015-03-01 05:39:31   
970     2015-03-01 05:39:34  55.825046  37.834022 2015-03-01 05:39:34   
...                     ...        ...        ...                 ...   
5048614 2021-08-27 17:12:18  55.604352  37.497382 2021-08-27 17:12:18   
5048615 2021-08-27 17:12:21  55.604120  37.497680 2021-08-27 17:12:21   
5048616 2021-08-27 17:12:23  55.603934  37.497906 2021-08-27 17:12:23   
5048617 2021-08-27 17:12:26  55.603682  37.498205 2021-08-27 17:12:26   
5048618 2021-08-27 17:12:29  55.603522  37.498388 2021-08-27 17:12:29   

                 driver_hash  fraud  gps_delta  gps_distance  gps_speed  \
966      4633179079544742811      0        3.0           4.0   1.333333   
967      4633179079544742811      0        3.0           4.0   1.333333   
968      4633179079544742811      0        3.0           4.0   1.333333   
969      4633179079544742811      0        3.0           2.0   0.666667   
970      4633179079544742811      0        3.0           1.0   0.333333   
...                      ...    ...        ...           ...        ...   
5048614  2423204062901461132     -1        3.0          30.0  10.000000   
5048615  2423204062901461132     -1        3.0          32.0  10.666667   
5048616  2423204062901461132     -1        2.0          25.0  12.500000   
5048617  2423204062901461132     -1        3.0          34.0  11.333333   
5048618  2423204062901461132     -1        3.0          21.0   7.000000   

         gps_accel  ...             ac_time      ac_x      ac_y      ac_z  \
966       0.000000  ... 2015-03-01 05:42:20  0.133682  8.409241  4.568481   
967       0.000000  ... 2015-03-01 05:42:20  0.133682  8.409241  4.568481   
968       0.000000  ... 2015-03-01 05:42:20  0.133682  8.409241  4.568481   
969      -0.222222  ... 2015-03-01 05:42:20  0.133682  8.409241  4.568481   
970      -0.111111  ... 2015-03-01 05:42:20  0.133682  8.409241  4.568481   
...            ...  ...                 ...       ...       ...       ...   
5048614  -1.000000  ... 2021-08-27 17:09:29  0.294487  9.339781  3.356671   
5048615   0.222222  ... 2021-08-27 17:09:29  0.294487  9.339781  3.356671   
5048616   0.916666  ... 2021-08-27 17:09:29  0.294487  9.339781  3.356671   
5048617  -0.388889  ... 2021-08-27 17:09:29  0.294487  9.339781  3.356671   
5048618  -1.444444  ... 2021-08-27 17:09:29  0.294487  9.339781  3.356671   

            ac_lat     ac_lon  ac_delta  ac_distance  ac_speed  ac_accel  
966      55.825185  37.833479    3600.0      10000.0  2.777778 -0.027006  
967      55.825185  37.833479    3600.0      10000.0  2.777778 -0.027006  
968      55.825185  37.833479    3600.0      10000.0  2.777778 -0.027006  
969      55.825185  37.833479    3600.0      10000.0  2.777778 -0.027006  
970      55.825185  37.833479    3600.0      10000.0  2.777778 -0.027006  
...            ...        ...       ...          ...       ...       ...  
5048614  55.604776  37.492613      60.0        246.0  4.100000 -1.598333  
5048615  55.604776  37.492613      60.0        246.0  4.100000 -1.598333  
5048616  55.604776  37.492613      60.0        246.0  4.100000 -1.598333  
5048617  55.604776  37.492613      60.0        246.0  4.100000 -1.598333  
5048618  55.604776  37.492613      60.0        246.0  4.100000 -1.598333  

[3025840 rows x 28 columns]

In [13]:
df_routs["route_id"] = routs_idx
describe(df_routs)

dtypes        count                           mean  \
time           datetime64[ns]      3025840  2020-07-14 13:30:11.094565888   
lat                   float64  3.02584e+06                        55.7496   
lon                   float64  3.02584e+06                        37.6015   
gps_time       datetime64[ns]      3025840  2020-07-14 13:30:09.230023936   
driver_hash             int64  3.02584e+06                    3.44787e+17   
fraud                   int64  3.02584e+06                       -0.75358   
gps_delta             float64  3.02584e+06                        2.84298   
gps_distance          float64  3.02584e+06                        17.5379   
gps_speed             float64  3.02584e+06                        6.61276   
gps_accel             float64  3.02584e+06                      -0.101907   
tm_delta              float64  3.02584e+06                        2.84403   
tm_distance           float64  3.02584e+06                        18.4506   
tm_speed              float64  3.02584e+06                        7.46159   
tm_accel              float64  3.02584e+06                       0.159088   
diff_time             float64  3.02584e+06                      0.0947145   
diff_distance         float64  3.02584e+06                       0.953821   
diff_speed            float64  3.02584e+06                       0.890091   
diff_accel            float64  3.02584e+06                       0.612109   
ac_time        datetime64[ns]      3025840  2020-07-14 13:30:08.372115456   
ac_x                  float64  3.02584e+06                         0.3195   
ac_y                  float64  3.02584e+06                        7.87314   
ac_z                  float64  3.02584e+06                        3.87407   
ac_lat                float64  3.02584e+06                        55.7497   
ac_lon                float64  3.02584e+06                        37.6013   
ac_delta              float64  3.02584e+06                        69.9641   
ac_distance           float64  3.02584e+06                        294.157   
ac_speed              float64  3.02584e+06                        66.2798   
ac_accel              float64  3.02584e+06                        24.3204   
route_id                int64  3.02584e+06                         263631   

                               min                            25%  \
time           2015-03-01 05:39:22  2020-11-13 02:43:43.249999872   
lat                          42.98                        55.6758   
lon                        36.3096                        37.4998   
gps_time       2015-03-01 05:39:22  2020-11-13 02:43:43.249999872   
driver_hash           -9.21858e+18                   -4.08039e+18   
fraud                           -1                             -1   
gps_delta                        0                              2   
gps_distance                     0                              0   
gps_speed                        0                              0   
gps_accel                     -100                      -0.222222   
tm_delta                         0                              2   
tm_distance                      0                              0   
tm_speed                         0                              0   
tm_accel                      -100                      -0.222222   
diff_time                        0                              0   
diff_distance                    0                              0   
diff_speed                       0                              0   
diff_accel                       0                              0   
ac_time        2015-03-01 05:42:20            2020-11-13 02:43:43   
ac_x                       -42.618                      -0.341156   
ac_y                       -41.359                        7.82449   
ac_z                      -28.9492                        2.15505   
ac_lat                     55.3625                        55.6759   
ac_lon                     36.3147                      

(3025840, 29)

In [14]:
df_routs.to_csv(f"{DATA_PATH}/matched_routs.csv", index=False)
'Done'

'Done'